Augmentation

-- Preprocess action tokens in raw, unlabeled trajectories so that LMs (explainer, baseline...) can make predictions to label them with instructions.

In [1]:
import os
os.environ['ALFRED_ROOT'] = '/root/home/legg/alfred/'

import sys
sys.path.append(os.path.join(os.environ['ALFRED_ROOT']))
sys.path.append(os.path.join(os.environ['ALFRED_ROOT'], 'models'))

import torch
import pprint
import json
from data.preprocess import Dataset
from importlib import import_module, reload
from argparse import ArgumentDefaultsHelpFormatter, ArgumentParser

In [2]:
parser = ArgumentParser(formatter_class=ArgumentDefaultsHelpFormatter)
args = parser.parse_args('')

# settings
args.data = '/root/media/legg/data-850-evo/json_data_augmentation_20200820/'
# args.splits = '/root/data_alfred/splits/debug_20201210.json'
args.splits = '/root/home/legg/data_alfred/splits/sample_failed_20200820.json'
args.pframe = 300
args.fast_epoch = False

## SPLITS

In [3]:
with open(args.splits, 'r') as f:
    splits = json.load(f)

In [4]:
len(splits['augmentation'])

7649

In [5]:
splits['augmentation'][:2]

[{'task': 'look_at_obj_in_light-BaseballBat-None-DeskLamp-301/trial_T20200814_164125_595727',
  'repeat_idx': 0,
  'full_traj_success': False,
  'collected_subgoals': 2},
 {'task': 'look_at_obj_in_light-BaseballBat-None-DeskLamp-324/trial_T20200814_164653_293251',
  'repeat_idx': 0,
  'full_traj_success': True,
  'collected_subgoals': 5}]

## EXPLAINER

In [6]:
model_name = 'model_seq2seq_per_subgoal,name_v2_epoch_40_obj_instance_enc_max_pool_dec_aux_loss_weighted_bce_1to2'
EXPLAINER = f'/root/home/hoyeung/blob_alfred_data/exp_all/{model_name}/net_epoch_32.pth'
args.pp_folder = 'pp_' + model_name

In [7]:
ckpt = torch.load(EXPLAINER)
ckpt['vocab']

{'action_high': Vocab(93), 'word': Vocab(2360), 'action_low': Vocab(15)}

In [8]:
dataset = Dataset(args, ckpt['vocab'])
dataset.preprocess_splits(splits, preprocess_lang=False, train_vocab=False, save_vocab_to_dout=False, augmentation_mode=True)

  0% (3 of 11947) |                      | Elapsed Time: 0:00:00 ETA:   0:07:10

Preprocessing augmentation
[{'task': 'pick_and_place_simple-CellPhone-None-Sofa-224/trial_T20190912_062415_255725', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 5}, {'task': 'pick_heat_then_place_in_recep-Tomato-None-DiningTable-19/trial_T20190911_051611_152502', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 7}, {'task': 'pick_cool_then_place_in_recep-Tomato-None-Microwave-20/trial_T20190911_220048_789694', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 7}, {'task': 'pick_and_place_simple-CellPhone-None-Dresser-314/trial_T20190910_153622_489437', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 4}, {'task': 'pick_and_place_simple-CreditCard-None-SideTable-313/trial_T20190913_140646_900196', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 4}, {'task': 'pick_cool_then_place_in_recep-AppleSliced-None-SinkBasin-7/trial_T20190910_135634_526097', 'repeat_idx': 0, 'full_traj_success': True, 'collect

100% (11947 of 11947) |##################| Elapsed Time: 0:05:16 Time:  0:05:16


#### Explainer Output Sanity Check

In [10]:
# results for each trajectory is saved to args.data/<task name>/<trial name>/pp_<model name>
!ls -l /root/media/legg/data-850-evo/json_data_augmentation_20200820/pick_two_obj_and_place-WineBottle-None-Shelf-1/trial_T20200818_043540_223173

total 33544
-rwxrwxrwx 1 user user 27998565 Aug 27  2020 feat_conv.pt
-rwxrwxrwx 1 user user  6249195 Aug 27  2020 metadata_states.json
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_baseline
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_explainer
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_model:seq2seq_nl_with_frames,name:v1.5_epoch_50_high_level_instrs
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_model:seq2seq_per_subgoal,name:v2_epoch_35_baseline
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_model:seq2seq_per_subgoal,name:v2_epoch_40_obj_instance_enc_max_pool_dec_aux_loss_weighted_bce_1to2
drwxrwxrwx 2 user user    12288 Aug 27  2020 raw_images
-rwxrwxrwx 1 user user    62266 Aug 27  2020 traj_data.json


In [10]:
!ls -l /root/data_alfred/unlabeled_12k_20201206/seen/pick_clean_then_place_in_recep-Fork-None-Drawer-7/trial_T20190910_031914_887703/pp_model_seq2seq_per_subgoal,name_v2_epoch_40_obj_instance_enc_max_pool_dec_aux_loss_weighted_bce_1to2

total 360
-rw-r--r-- 1 root root 367725 Dec 27 21:16 ann_0.json


In [11]:
with open('/root/data_alfred/unlabeled_12k_20201206/seen/pick_and_place_with_movable_recep-Knife-Pot-CounterTop-1/trial_T20190918_220230_284512/pp_model_seq2seq_per_subgoal,name_v2_epoch_40_obj_instance_enc_max_pool_dec_aux_loss_weighted_bce_1to2/ann_0.json', 'r') as f:
    ann = json.load(f)

In [12]:
ann['num']['action_low']

[[{'action': 3,
   'action_high_args': {},
   'centroid': [-1, -1],
   'high_idx': 0,
   'mask': None,
   'valid_interact': 0},
  {'action': 5,
   'action_high_args': {},
   'centroid': [-1, -1],
   'high_idx': 0,
   'mask': None,
   'valid_interact': 0},
  {'action': 4,
   'action_high_args': {},
   'centroid': [-1, -1],
   'high_idx': 0,
   'mask': None,
   'valid_interact': 0},
  {'action': 5,
   'action_high_args': {},
   'centroid': [-1, -1],
   'high_idx': 0,
   'mask': None,
   'valid_interact': 0},
  {'action': 4,
   'action_high_args': {},
   'centroid': [-1, -1],
   'high_idx': 0,
   'mask': None,
   'valid_interact': 0},
  {'action': 4,
   'action_high_args': {},
   'centroid': [-1, -1],
   'high_idx': 0,
   'mask': None,
   'valid_interact': 0},
  {'action': 4,
   'action_high_args': {},
   'centroid': [-1, -1],
   'high_idx': 0,
   'mask': None,
   'valid_interact': 0},
  {'action': 4,
   'action_high_args': {},
   'centroid': [-1, -1],
   'high_idx': 0,
   'mask': None,
 

## EXPLAINER ENC STATE ONLY

In [6]:
model_name = 'model:seq2seq_per_subgoal,name:v2_epoch_40_obj_instance_enc_max_pool_dec_axu_loss_none'
EXPLAINER_ENC_ONLY = f'/root/home/legg/blob_alfred_data/exp_all/{model_name}/net_epoch_5.pth'
args.pp_folder = 'pp_' + model_name

In [7]:
# del(ckpt)
ckpt = torch.load(EXPLAINER_ENC_ONLY)
ckpt['vocab']

{'action_high': Vocab(93), 'word': Vocab(2360), 'action_low': Vocab(15)}

In [9]:
dataset = Dataset(args, ckpt['vocab'])
dataset.preprocess_splits(splits, preprocess_lang=False, train_vocab=False, save_vocab_to_dout=False, augmentation_mode=True)

  0% (35 of 7649) |                      | Elapsed Time: 0:00:00 ETA:   0:00:22

Preprocessing augmentation
[{'task': 'look_at_obj_in_light-BaseballBat-None-DeskLamp-301/trial_T20200814_164125_595727', 'repeat_idx': 0, 'full_traj_success': False, 'collected_subgoals': 2}, {'task': 'look_at_obj_in_light-BaseballBat-None-DeskLamp-324/trial_T20200814_164653_293251', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 5}, {'task': 'look_at_obj_in_light-BasketBall-None-DeskLamp-319/trial_T20200814_165040_882757', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 5}, {'task': 'look_at_obj_in_light-BasketBall-None-DeskLamp-327/trial_T20200814_165217_576013', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 5}, {'task': 'look_at_obj_in_light-Book-None-DeskLamp-301/trial_T20200814_165504_049184', 'repeat_idx': 0, 'full_traj_success': False, 'collected_subgoals': 2}, {'task': 'look_at_obj_in_light-Book-None-DeskLamp-327/trial_T20200814_170059_770461', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 5}, {'task':

100% (7649 of 7649) |####################| Elapsed Time: 0:00:32 Time:  0:00:32


In [10]:
# results for each trajectory is saved to args.data/<task name>/<trial name>/pp_<model name>
!ls -l /root/media/legg/data-850-evo/json_data_augmentation_20200820/pick_two_obj_and_place-WineBottle-None-Shelf-1/trial_T20200818_043540_223173

total 33548
-rwxrwxrwx 1 user user 27998565 Aug 27  2020 feat_conv.pt
-rwxrwxrwx 1 user user  6249195 Aug 27  2020 metadata_states.json
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_baseline
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_explainer
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_model:seq2seq_nl_with_frames,name:v1.5_epoch_50_high_level_instrs
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_model:seq2seq_per_subgoal,name:v2_epoch_35_baseline
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_model:seq2seq_per_subgoal,name:v2_epoch_40_obj_instance_enc_max_pool_dec_aux_loss_weighted_bce_1to2
drwxr-xr-x 2 root root     4096 Jun 23 05:16 pp_model:seq2seq_per_subgoal,name:v2_epoch_40_obj_instance_enc_max_pool_dec_axu_loss_none
drwxrwxrwx 2 user user    12288 Aug 27  2020 raw_images
-rwxrwxrwx 1 user user    62266 Aug 27  2020 traj_data.json


## EXPLAINER AUX LOSS ONLY

In [6]:
model_name = 'model:seq2seq_per_subgoal,name:v2_epoch_40_obj_instance_enc_none_dec_axu_loss_weighted_bce_1to2'
EXPLAINER_AUX_ONLY = f'/root/home/legg/blob_alfred_data/exp_all/{model_name}/net_epoch_32.pth'
args.pp_folder = 'pp_' + model_name

In [9]:
# del(ckpt)
ckpt = torch.load(EXPLAINER_AUX_ONLY)
ckpt['vocab']

{'action_high': Vocab(93), 'word': Vocab(2360), 'action_low': Vocab(15)}

In [10]:
dataset = Dataset(args, ckpt['vocab'])
dataset.preprocess_splits(splits, preprocess_lang=False, train_vocab=False, save_vocab_to_dout=False, augmentation_mode=True)

  0% (37 of 7649) |                      | Elapsed Time: 0:00:00 ETA:   0:00:20

Preprocessing augmentation
[{'task': 'look_at_obj_in_light-BaseballBat-None-DeskLamp-301/trial_T20200814_164125_595727', 'repeat_idx': 0, 'full_traj_success': False, 'collected_subgoals': 2}, {'task': 'look_at_obj_in_light-BaseballBat-None-DeskLamp-324/trial_T20200814_164653_293251', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 5}, {'task': 'look_at_obj_in_light-BasketBall-None-DeskLamp-319/trial_T20200814_165040_882757', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 5}, {'task': 'look_at_obj_in_light-BasketBall-None-DeskLamp-327/trial_T20200814_165217_576013', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 5}, {'task': 'look_at_obj_in_light-Book-None-DeskLamp-301/trial_T20200814_165504_049184', 'repeat_idx': 0, 'full_traj_success': False, 'collected_subgoals': 2}, {'task': 'look_at_obj_in_light-Book-None-DeskLamp-327/trial_T20200814_170059_770461', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 5}, {'task':

100% (7649 of 7649) |####################| Elapsed Time: 0:00:32 Time:  0:00:32


In [11]:
# results for each trajectory is saved to args.data/<task name>/<trial name>/pp_<model name>
!ls -l /root/media/legg/data-850-evo/json_data_augmentation_20200820/pick_two_obj_and_place-WineBottle-None-Shelf-1/trial_T20200818_043540_223173

total 33552
-rwxrwxrwx 1 user user 27998565 Aug 27  2020 feat_conv.pt
-rwxrwxrwx 1 user user  6249195 Aug 27  2020 metadata_states.json
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_baseline
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_explainer
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_model:seq2seq_nl_with_frames,name:v1.5_epoch_50_high_level_instrs
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_model:seq2seq_per_subgoal,name:v2_epoch_35_baseline
drwxrwxrwx 2 user user     4096 Aug 27  2020 pp_model:seq2seq_per_subgoal,name:v2_epoch_40_obj_instance_enc_max_pool_dec_aux_loss_weighted_bce_1to2
drwxr-xr-x 2 root root     4096 Jun 23 05:16 pp_model:seq2seq_per_subgoal,name:v2_epoch_40_obj_instance_enc_max_pool_dec_axu_loss_none
drwxr-xr-x 2 root root     4096 Jun 23 06:12 pp_model:seq2seq_per_subgoal,name:v2_epoch_40_obj_instance_enc_none_dec_axu_loss_weighted_bce_1to2
drwxrwxrwx 2 user user    12288 Aug 27  2020 raw_images
-rwxrwxrwx 1 user user    62266 Aug 27  2020 traj_da

## BASELINE

In [17]:
model_name = 'model_seq2seq_per_subgoal,name_v2_epoch_35_baseline'
BASELINE = f'/root/home/hoyeung/blob_alfred_data/exp_all/{model_name}/net_epoch_29.pth'
args.pp_folder = 'pp_' + model_name

In [18]:
ckpt = torch.load(BASELINE)
ckpt['vocab']

{'action_high': Vocab(93), 'word': Vocab(2360), 'action_low': Vocab(15)}

In [19]:
dataset = Dataset(args, ckpt['vocab'])
dataset.preprocess_splits(splits, preprocess_lang=False, train_vocab=False, save_vocab_to_dout=False, augmentation_mode=True)

  0% (6 of 11947) |                      | Elapsed Time: 0:00:00 ETA:   0:04:16

Preprocessing augmentation
[{'task': 'pick_and_place_simple-CellPhone-None-Sofa-224/trial_T20190912_062415_255725', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 5}, {'task': 'pick_heat_then_place_in_recep-Tomato-None-DiningTable-19/trial_T20190911_051611_152502', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 7}, {'task': 'pick_cool_then_place_in_recep-Tomato-None-Microwave-20/trial_T20190911_220048_789694', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 7}, {'task': 'pick_and_place_simple-CellPhone-None-Dresser-314/trial_T20190910_153622_489437', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 4}, {'task': 'pick_and_place_simple-CreditCard-None-SideTable-313/trial_T20190913_140646_900196', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 4}, {'task': 'pick_cool_then_place_in_recep-AppleSliced-None-SinkBasin-7/trial_T20190910_135634_526097', 'repeat_idx': 0, 'full_traj_success': True, 'collect

100% (11947 of 11947) |##################| Elapsed Time: 0:04:50 Time:  0:04:50


In [20]:
# results for each trajectory is saved to args.data/<task name>/<trial name>/pp_<model name>
!ls -l /root/data_alfred/unlabeled_12k_20201206/seen/pick_clean_then_place_in_recep-Fork-None-Drawer-7/trial_T20190910_031914_887703/

total 43148
-rw-r--r-- 1 root root 35023205 Dec  9 11:20 feat_conv.pt
-rw-r--r-- 1 root root  9088534 Dec 14 07:51 metadata_states.json
drwxr-xr-x 2 root root       28 Sep 10  2019 pddl_states
drwxr-xr-x 2 root root       24 Dec 27 21:30 pp_model_seq2seq_per_subgoal,name_v2_epoch_35_baseline
drwxr-xr-x 2 root root       24 Dec 27 21:16 pp_model_seq2seq_per_subgoal,name_v2_epoch_40_obj_instance_enc_max_pool_dec_aux_loss_weighted_bce_1to2
drwxr-xr-x 2 root root       24 Dec 27 21:22 pp_model:seq2seq_per_subgoal,name:v2_epoch_40_obj_instance_enc_max_pool_dec_axu_loss_none
drwxr-xr-x 2 root root    12288 Nov 30 12:21 raw_images
-rw-r--r-- 1 root root    52288 Sep 10  2019 traj_data.json


## GOAL EXPLAINER

In [21]:
model_name = 'model_seq2seq_nl_with_frames,name_v1.5_epoch_50_high_level_instrs'
GOAL_EXPLAINER = f'/root/home/hoyeung/blob_alfred_data/exp_all/{model_name}/net_epoch_10.pth'
args.pp_folder = 'pp_' + model_name

In [22]:
del(ckpt)
ckpt = torch.load(GOAL_EXPLAINER)
ckpt['vocab']

{'word': Vocab(2360), 'action_low': Vocab(15), 'action_high': Vocab(93)}

In [23]:
dataset = Dataset(args, ckpt['vocab'])
dataset.preprocess_splits(splits, preprocess_lang=False, train_vocab=False, save_vocab_to_dout=False, augmentation_mode=True)

  0% (6 of 11947) |                      | Elapsed Time: 0:00:00 ETA:   0:04:05

Preprocessing augmentation
[{'task': 'pick_and_place_simple-CellPhone-None-Sofa-224/trial_T20190912_062415_255725', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 5}, {'task': 'pick_heat_then_place_in_recep-Tomato-None-DiningTable-19/trial_T20190911_051611_152502', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 7}, {'task': 'pick_cool_then_place_in_recep-Tomato-None-Microwave-20/trial_T20190911_220048_789694', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 7}, {'task': 'pick_and_place_simple-CellPhone-None-Dresser-314/trial_T20190910_153622_489437', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 4}, {'task': 'pick_and_place_simple-CreditCard-None-SideTable-313/trial_T20190913_140646_900196', 'repeat_idx': 0, 'full_traj_success': True, 'collected_subgoals': 4}, {'task': 'pick_cool_then_place_in_recep-AppleSliced-None-SinkBasin-7/trial_T20190910_135634_526097', 'repeat_idx': 0, 'full_traj_success': True, 'collect

100% (11947 of 11947) |##################| Elapsed Time: 0:04:43 Time:  0:04:43


In [24]:
# results for each trajectory is saved to args.data/<task name>/<trial name>/pp_<model name>
!ls -l /root/data_alfred/unlabeled_12k_20201206/seen/pick_clean_then_place_in_recep-Fork-None-Drawer-7/trial_T20190910_031914_887703/

total 43148
-rw-r--r-- 1 root root 35023205 Dec  9 11:20 feat_conv.pt
-rw-r--r-- 1 root root  9088534 Dec 14 07:51 metadata_states.json
drwxr-xr-x 2 root root       28 Sep 10  2019 pddl_states
drwxr-xr-x 2 root root       24 Dec 27 21:35 pp_model_seq2seq_nl_with_frames,name_v1.5_epoch_50_high_level_instrs
drwxr-xr-x 2 root root       24 Dec 27 21:30 pp_model_seq2seq_per_subgoal,name_v2_epoch_35_baseline
drwxr-xr-x 2 root root       24 Dec 27 21:16 pp_model_seq2seq_per_subgoal,name_v2_epoch_40_obj_instance_enc_max_pool_dec_aux_loss_weighted_bce_1to2
drwxr-xr-x 2 root root       24 Dec 27 21:22 pp_model:seq2seq_per_subgoal,name:v2_epoch_40_obj_instance_enc_max_pool_dec_axu_loss_none
drwxr-xr-x 2 root root    12288 Nov 30 12:21 raw_images
-rw-r--r-- 1 root root    52288 Sep 10  2019 traj_data.json


In [25]:
!ls -l /root/data_alfred/unlabeled_12k_20201206/seen/pick_clean_then_place_in_recep-Fork-None-Drawer-7/trial_T20190910_031914_887703/pp_model_seq2seq_nl_with_frames,name_v1.5_epoch_50_high_level_instrs

total 360
-rw-r--r-- 1 root root 367725 Dec 27 21:35 ann_0.json
